# Import libraries

In [1]:
# Cell 1
import tensorflow as tf
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import io
import os
from sklearn.preprocessing import MinMaxScaler
from tqdm import tqdm
from sklearn.metrics import mean_absolute_error, mean_squared_error, mean_absolute_percentage_error
import random
from keras.models import Sequential
from keras.layers import LSTM, Dense
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score
from tensorflow.keras.models import load_model
from keras.utils import custom_object_scope
from tensorflow.keras.layers import Bidirectional, SimpleRNN, Dense
import time
from xgboost import XGBRegressor
from glob import glob
import logging
import re
import shutil
import traceback
from datetime import datetime, timedelta

# Pre process files

In [ ]:
import tensorflow as tf
import pandas as pd
import numpy as np
import os
from sklearn.preprocessing import MinMaxScaler

def create_output_directories():
    """Create directories for original and preprocessed data"""
    current_dir = os.getcwd()
    original_dir = os.path.join(current_dir, 'files', 'original_absolute')
    preprocessed_dir = os.path.join(current_dir, 'files', 'pre_processed_data')
    
    if not os.path.exists(original_dir):
        os.makedirs(original_dir)
    if not os.path.exists(preprocessed_dir):
        os.makedirs(preprocessed_dir)
    
    return original_dir, preprocessed_dir

def upload_and_process_files(directory, num_files_to_use=None):
    """Process GPS files following SC-BETA-VAE-GAN methodology"""
    tenv3_files = [f for f in os.listdir(directory) if f.endswith(".tenv3")]
    
    if num_files_to_use:
        tenv3_files = tenv3_files[:num_files_to_use]
    
    num_files = len(tenv3_files)
    if num_files == 0:
        raise ValueError(f"No .tenv3 files found in {directory}")
    
    data_frames = []  
    original_data_frames = []  
    processed_data = []  
    scalers = []
    input_filenames = []
    
    # Create output directories
    original_dir = 'files/original_absolute'
    preprocessed_dir = 'files/pre_processed_data'
    os.makedirs(original_dir, exist_ok=True)
    os.makedirs(preprocessed_dir, exist_ok=True)
    
    for i, filename in enumerate(tenv3_files):
        print(f"Processing file {i+1}...")
        file_path = os.path.join(directory, filename)
        input_filenames.append(filename)
        
        # Read header and data
        with open(file_path, 'r') as f:
            header = f.readline().strip()
        column_names = header.split()
        df = pd.read_csv(file_path, skiprows=1, sep=r'\s+', names=column_names)
        
        # Save original data
        original_data_frames.append(df.copy())
        data_frames.append(df.copy())
        
        # Save to original_absolute folder
        original_filename = os.path.join(original_dir, f"original_{filename}")
        df.to_csv(original_filename, sep=' ', index=False, header=False)
        
        # Process coordinates
        coordinates = df[['__east(m)', '_north(m)', '____up(m)']].values
        scaler = MinMaxScaler()
        normalized_coords = scaler.fit_transform(coordinates)
        scalers.append(scaler)
        
        # Store processed data (this is what we'll use for training)
        processed_data.append(normalized_coords)
        
        # Save preprocessed data
        processed_df = pd.DataFrame(
            normalized_coords,
            columns=['east_normalized', 'north_normalized', 'up_normalized']
        )
        preprocessed_filename = os.path.join(preprocessed_dir, f"preprocessed_{filename}")
        processed_df.to_csv(preprocessed_filename, sep=' ', index=False, header=False)
    
    avg_data_points = int(np.mean([len(data) for data in processed_data]))
    
    return data_frames, processed_data, scalers, avg_data_points, input_filenames, original_data_frames

print("Starting preprocessing...")
try:
    input_dir = os.path.join('..', 'dataset', 'train')
    data_frames, processed_data, scalers, avg_data_points, input_filenames, original_data_frames = upload_and_process_files(input_dir)
    
    print(f"\nProcessing Summary:")
    print(f"Number of processed files: {len(processed_data)}")
    print(f"Average data points: {avg_data_points}")
    print("Processing completed successfully!")
    
except Exception as e:
    print(f"An error occurred: {str(e)}")
    import traceback
    print("\nFull error traceback:")
    print(traceback.format_exc())

Starting preprocessing...
Processing file 1...
Processing file 2...
Processing file 3...
Processing file 4...
Processing file 5...
Processing file 6...
Processing file 7...
Processing file 8...
Processing file 9...
Processing file 10...
Processing file 11...
Processing file 12...
Processing file 13...
Processing file 14...
Processing file 15...
Processing file 16...
Processing file 17...
Processing file 18...
Processing file 19...
Processing file 20...

Processing Summary:
Number of processed files: 20
Average data points: 5525
Processing completed successfully!


# Function to enhance processed data

In [3]:
def safe_normalize(values):
    """
    Safely normalize values, handling cases where min and max are the same
    """
    min_val = np.min(values)
    max_val = np.max(values)
    if min_val == max_val:
        return np.zeros_like(values)  # Return zeros if no variation
    return (values - min_val) / (max_val - min_val)

def enhance_gps_quality(processed_data, original_data_frames, maintain_scbeta=True):
    """
    Enhanced quality function with safe normalization and debugging
    """
    enhanced_data = []
    
    for idx, (proc_data, orig_df) in enumerate(zip(processed_data, original_data_frames)):
        print(f"\nProcessing dataset {idx}")
        
        # Debug original values
        print(f"Original e0 range: [{orig_df['_e0(m)'].min()}, {orig_df['_e0(m)'].max()}]")
        print(f"Original n0 range: [{orig_df['____n0(m)'].min()}, {orig_df['____n0(m)'].max()}]")
        print(f"Original u0 range: [{orig_df['u0(m)'].min()}, {orig_df['u0(m)'].max()}]")
        
        # Extract measurement quality
        quality_metrics = {
            'uncertainties': {
                'east': orig_df['sig_e(m)'].values,
                'north': orig_df['sig_n(m)'].values,
                'up': orig_df['sig_u(m)'].values
            },
            'correlations': {
                'en': orig_df['__corr_en'].values,
                'eu': orig_df['__corr_eu'].values,
                'nu': orig_df['__corr_nu'].values
            }
        }
        
        # Calculate normalized reference coordinates using safe normalization
        reference_coords = {
            'east': safe_normalize(orig_df['_e0(m)'].values),
            'north': safe_normalize(orig_df['____n0(m)'].values),
            'up': safe_normalize(orig_df['u0(m)'].values)
        }
        
        print("\nReference coordinate ranges after normalization:")
        print(f"East: [{reference_coords['east'].min()}, {reference_coords['east'].max()}]")
        print(f"North: [{reference_coords['north'].min()}, {reference_coords['north'].max()}]")
        print(f"Up: [{reference_coords['up'].min()}, {reference_coords['up'].max()}]")
        
        # Calculate quality weights with adjusted scaling
        uncertainty_matrix = np.column_stack([
            quality_metrics['uncertainties']['east'],
            quality_metrics['uncertainties']['north'],
            quality_metrics['uncertainties']['up']
        ])
        
        # Safe normalization for uncertainties
        uncertainty_matrix = np.apply_along_axis(safe_normalize, 0, uncertainty_matrix)
        weights = 1 - uncertainty_matrix
        
        print("\nWeight ranges:")
        print(f"East weights: [{weights[:, 0].min()}, {weights[:, 0].max()}]")
        print(f"North weights: [{weights[:, 1].min()}, {weights[:, 1].max()}]")
        print(f"Up weights: [{weights[:, 2].min()}, {weights[:, 2].max()}]")
        
        # Get correlation matrix
        correlation_matrix = np.array([
            quality_metrics['correlations']['en'],
            quality_metrics['correlations']['eu'],
            quality_metrics['correlations']['nu']
        ])
        
        # Enhance coordinates
        enhanced_coords = proc_data.copy()
        
        if maintain_scbeta:
            reference_arrays = [
                reference_coords['east'],
                reference_coords['north'],
                reference_coords['up']
            ]
            
            for i in range(3):
                enhanced_coords[:, i] = enhance_coordinate(
                    enhanced_coords[:, i],
                    weights[:, i],
                    correlation_matrix[i],
                    reference_arrays[i]
                )
                
                print(f"\nComponent {i} enhancement results:")
                print(f"Original range: [{proc_data[:, i].min()}, {proc_data[:, i].max()}]")
                print(f"Enhanced range: [{enhanced_coords[:, i].min()}, {enhanced_coords[:, i].max()}]")
        
        # Validate with debugging
        validation_result = validate_gps_coordinates(enhanced_coords, orig_df, debug=True)
        
        if validation_result:
            print(f"Dataset {idx}: Enhancement successful")
            enhanced_data.append(enhanced_coords)
        else:
            print(f"Warning: Enhancement validation failed for dataset {idx}, using original data")
            enhanced_data.append(proc_data)
    
    return enhanced_data

def validate_gps_coordinates(coords, orig_df, debug=False):
    """
    Validate coordinates with debugging
    """
    if debug:
        print("\nValidation Results:")
        print(f"Coordinate range: [{coords.min()}, {coords.max()}]")
        
    # Range validation
    range_valid = np.all(coords >= -0.1) and np.all(coords <= 1.1)
    if debug:
        print(f"Range validation: {range_valid}")
    
    # Jump validation
    jump_threshold = 0.15
    jumps = np.abs(np.diff(coords, axis=0))
    max_jump = np.max(jumps)
    jumps_valid = np.all(jumps < jump_threshold)
    
    if debug:
        print(f"Maximum jump: {max_jump}")
        print(f"Jump validation: {jumps_valid}")
    
    # Time series validation
    time_series_valid = validate_time_series(coords)
    if debug:
        print(f"Time series validation: {time_series_valid}")
    
    return range_valid and jumps_valid and time_series_valid

# def validate_time_series(coords):
#     """
#     Validate temporal consistency with debugging
#     """
#     max_allowed_jump = 3 * np.std(coords, axis=0)
#     jumps = np.abs(np.diff(coords, axis=0))
    
#     valid = np.all(jumps < max_allowed_jump)
#     if not valid:
#         print(f"Max allowed jump: {max_allowed_jump}")
#         print(f"Actual max jump: {np.max(jumps, axis=0)}")
    
#     return valid

# Add debugging to enhance_coordinate function
def enhance_coordinate(coord, weights, correlations, reference):
    """
    Enhanced coordinate processing with adjusted deviation handling
    """
    # Apply weight-based smoothing
    weighted_coord = coord * weights
    
    # Compare with normalized reference
    ref_diff = np.abs(weighted_coord - reference)
    
    # Use more lenient threshold for large deviations (5 std instead of 3)
    large_deviations = ref_diff > np.std(ref_diff) * 5
    
    if np.any(large_deviations):
        weighted_coord[large_deviations] = (
            weighted_coord[large_deviations] * 0.8 +  # Increased weight for original value
            coord[large_deviations] * 0.2
        )
    
    return weighted_coord

def validate_time_series(coords):
    """
    Validate temporal consistency with adjusted threshold
    """
    max_allowed_jump = 5 * np.std(coords, axis=0)  # Increased from 3 to 5
    jumps = np.abs(np.diff(coords, axis=0))
    
    return np.all(jumps < max_allowed_jump)

print("Original data statistics:")
print(f"Shape: {processed_data[0].shape}")
print(f"Range: [{processed_data[0].min()}, {processed_data[0].max()}]")

processed_data = enhance_gps_quality(processed_data, original_data_frames)

Original data statistics:
Shape: (5686, 3)
Range: [0.0, 1.0000000000000002]

Processing dataset 0
Original e0 range: [512, 512]
Original n0 range: [8833621, 8833621]
Original u0 range: [484, 484]

Reference coordinate ranges after normalization:
East: [0, 0]
North: [0, 0]
Up: [0, 0]

Weight ranges:
East weights: [0.0, 1.0]
North weights: [0.0, 1.0]
Up weights: [0.0, 1.0]

Component 0 enhancement results:
Original range: [0.0, 1.0]
Enhanced range: [0.0, 0.9055162350015519]

Component 1 enhancement results:
Original range: [0.0, 1.0000000000000002]
Enhanced range: [0.0, 0.97828060422852]

Component 2 enhancement results:
Original range: [0.0, 1.0000000000000002]
Enhanced range: [0.0, 0.9516142185664065]

Validation Results:
Coordinate range: [0.0, 0.97828060422852]
Range validation: True
Maximum jump: 0.672117720358262
Jump validation: False
Time series validation: True

Processing dataset 1
Original e0 range: [1737, 1737]
Original n0 range: [7968309, 7968309]
Original u0 range: [1494, 1

# Gap Identification

In [4]:
def identify_gaps(df, filename):
    """
    Identify gaps and missing coordinates in GPS time series data
    Args:
        df: DataFrame containing GPS data
        filename: Name of the GPS station file
    Returns:
        gaps_info: Dictionary containing gap and missing data information
    """
    # Convert dates to datetime
    df['date'] = pd.to_datetime(df['YYMMMDD'], format='%y%b%d')
    
    # Sort by date
    df = df.sort_values('date')
    
    # Identify missing coordinates
    missing_coords = df[df['__east(m)'].isna() & 
                       df['_north(m)'].isna() & 
                       df['____up(m)'].isna()]
    
    # Calculate time differences between consecutive measurements
    df['days_diff'] = df['date'].diff().dt.days
    
    # Identify gaps (where difference > 1 day)
    gaps = df[df['days_diff'] > 1].copy()
    
    # Store gap and missing data information
    gaps_info = {
        'station': filename,
        'total_gaps': len(gaps),
        'total_gap_days': gaps['days_diff'].sum() - len(gaps),
        'missing_coordinates_dates': missing_coords['YYMMMDD'].tolist(),
        'total_missing_coordinates': len(missing_coords),
        'gap_ranges': [],
        'gap_statistics': {}
    }
    
    if len(gaps) > 0:
        # Record each gap's details
        for idx, row in gaps.iterrows():
            prev_date = df.loc[idx-1, 'date']
            gap_length = row['days_diff'] - 1
            gaps_info['gap_ranges'].append({
                'start_date': prev_date.strftime('%Y-%m-%d'),
                'end_date': row['date'].strftime('%Y-%m-%d'),
                'length': gap_length
            })
        
        # Calculate gap statistics
        gap_lengths = [g['length'] for g in gaps_info['gap_ranges']]
        gaps_info['gap_statistics'] = {
            'min_length': min(gap_lengths),
            'max_length': max(gap_lengths),
            'mean_length': np.mean(gap_lengths),
            'median_length': np.median(gap_lengths)
        }
        
        # Categorize gaps
        gaps_info['gap_categories'] = {
            'short': len([g for g in gap_lengths if g <= 7]),
            'medium': len([g for g in gap_lengths if 7 < g <= 30]),
            'long': len([g for g in gap_lengths if g > 30])
        }
    
    return gaps_info, df

def fill_identified_gaps(df, gaps_info):
    """
    Fill both gaps and missing coordinates in GPS time series data.
    Args:
        df: DataFrame with GPS data
        gaps_info: Dictionary containing gap information from identify_gaps
    Returns:
        DataFrame with filled gaps and interpolated coordinates
    """
    df = df.copy()
    new_rows = []
    
    # First report missing coordinates
    if gaps_info['total_missing_coordinates'] > 0:
        print(f"\nDates with missing coordinates:")
        for date in gaps_info['missing_coordinates_dates']:
            print(f"  {date}")
    
    # Then handle gaps between dates
    if gaps_info['total_gaps'] > 0:
        print(f"\nGaps between dates:")
        for gap in gaps_info['gap_ranges']:
            print(f"  {gap['start_date']} to {gap['end_date']} ({gap['length']} days)")
            
            # Create rows for missing days
            start_date = pd.to_datetime(gap['start_date'])
            end_date = pd.to_datetime(gap['end_date'])
            
            date_range = pd.date_range(start_date + pd.Timedelta(days=1), 
                                     end_date - pd.Timedelta(days=1),
                                     freq='D')
            
            for date in date_range:
                new_row = {
                    'date': date,
                    'YYMMMDD': date.strftime('%y%b%d').upper(),
                    '__east(m)': np.nan,
                    '_north(m)': np.nan,
                    '____up(m)': np.nan
                }
                new_rows.append(new_row)
    
    # Add new rows and sort
    if new_rows:
        df_new = pd.DataFrame(new_rows)
        df = pd.concat([df, df_new], ignore_index=True)
    
    # Sort by date and interpolate all missing values
    df = df.sort_values('date')
    for col in ['__east(m)', '_north(m)', '____up(m)']:
        df[col] = df[col].interpolate(method='linear')
    
    return df

def process_and_fill_gaps(data_frames, input_filenames):
    """Process gaps and missing coordinates for all GPS stations."""
    processed_frames = []
    gaps_summary = []
    
    for df, filename in zip(data_frames, input_filenames):
        print(f"\nProcessing {filename}")
        
        # Identify gaps and missing coordinates
        gaps_info, df_with_dates = identify_gaps(df.copy(), filename)
        gaps_summary.append(gaps_info)
        
        # Fill gaps and interpolate coordinates
        processed_df = fill_identified_gaps(df_with_dates, gaps_info)
        processed_frames.append(processed_df)
        
        # Print summary
        print(f"Original points: {len(df)}")
        print(f"Missing coordinates: {gaps_info['total_missing_coordinates']}")
        print(f"Gaps: {gaps_info['total_gaps']}")
        print(f"Total gap days: {gaps_info['total_gap_days']}")
        print(f"Final points after filling: {len(processed_df)}")
        
    return processed_frames, gaps_summary

def save_processed_gps(processed_frames, input_filenames):
    """Save processed GPS data to imputed folder."""
    imputed_folder = 'imputed'
    os.makedirs(imputed_folder, exist_ok=True)
    
    for filename, df in zip(input_filenames, processed_frames):
        # Round coordinates to maintain precision
        cols = ['__east(m)', '_north(m)', '____up(m)']
        df[cols] = df[cols].round(6)
        
        # Save with original GPS data format
        save_path = os.path.join(imputed_folder, filename)
        df[['YYMMMDD'] + cols].to_csv(save_path, sep=' ', index=False, header=False)
        print(f"Processed data saved as: {filename}")

# Usage:
processed_frames, gaps_summary = process_and_fill_gaps(data_frames, input_filenames)
save_processed_gps(processed_frames, input_filenames)


Processing BLAS.tenv3

Gaps between dates:
  2012-03-24 to 2012-09-01 (160.0 days)
  2014-06-05 to 2014-08-21 (76.0 days)
  2020-12-23 to 2020-12-25 (1.0 days)
  2023-11-21 to 2023-11-23 (1.0 days)
  2023-12-18 to 2023-12-20 (1.0 days)
  2024-04-09 to 2024-04-11 (1.0 days)
  2024-07-23 to 2024-07-25 (1.0 days)
Original points: 5686
Missing coordinates: 0
Gaps: 7
Total gap days: 241.0
Final points after filling: 5927

Processing DGJG.tenv3

Gaps between dates:
  2012-07-09 to 2012-07-12 (2.0 days)
  2018-05-12 to 2018-05-14 (1.0 days)
  2020-03-24 to 2020-03-26 (1.0 days)
  2022-06-21 to 2022-06-23 (1.0 days)
  2023-10-18 to 2023-10-20 (1.0 days)
Original points: 5521
Missing coordinates: 0
Gaps: 5
Total gap days: 6.0
Final points after filling: 5527

Processing DKSG.tenv3

Gaps between dates:
  2007-09-05 to 2007-09-07 (1.0 days)
  2011-01-02 to 2011-03-04 (60.0 days)
  2011-03-05 to 2011-03-07 (1.0 days)
  2011-03-08 to 2011-03-10 (1.0 days)
  2011-03-22 to 2011-03-24 (1.0 days)
  20

# Convert format

In [14]:
import glob
def convert_to_simple_format(input_file, output_file):
    """
    Convert augmented GPS file from full format to simple format:
    From: full format with all columns
    To: YYMMMDD east north up
    
    Args:
        input_file (str): Path to input file with full format
        output_file (str): Path where simplified format will be saved
    """
    try:
        # Read the full format file
        with open(input_file, 'r') as f:
            lines = f.readlines()
        
        # Skip header line
        data_lines = lines[1:]
        
        # Process each line
        simplified_lines = []
        for line in data_lines:
            # Split the line by whitespace
            fields = line.strip().split()
            
            # Extract required fields
            # YYMMMDD is index 1
            # east is index 8 (__east(m))
            # north is index 10 (_north(m))
            # up is index 12 (____up(m))
            try:
                yymmmdd = fields[1]
                east = float(fields[8])
                north = float(fields[10])
                up = float(fields[12])
                
                # Format with 6 decimal places
                simplified_line = f"{yymmmdd} {east:.6f} {north:.6f} {up:.6f}\n"
                simplified_lines.append(simplified_line)
            except (IndexError, ValueError) as e:
                print(f"Error processing line: {line.strip()}")
                print(f"Error details: {str(e)}")
                continue
        
        # Write to output file
        with open(output_file, 'w') as f:
            f.writelines(simplified_lines)
            
        print(f"Successfully converted {input_file} to simplified format at {output_file}")
        return True
        
    except Exception as e:
        print(f"Error converting file {input_file}: {str(e)}")
        return False

def batch_convert_files(input_dir, output_dir):
    """
    Convert all augmented GPS files in a directory to simple format.
    
    Args:
        input_dir (str): Directory containing augmented files
        output_dir (str): Directory where simplified files will be saved
    """
    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)
    
    # Get all files in input directory
    input_files = glob.glob(os.path.join(input_dir, "*"))
    
    successful_conversions = 0
    failed_conversions = 0
    
    for input_file in input_files:
        # Create output filename
        base_name = os.path.basename(input_file)
        output_file = os.path.join(output_dir, f"{base_name}")
        
        # Convert file
        if convert_to_simple_format(input_file, output_file):
            successful_conversions += 1
        else:
            failed_conversions += 1
    
    print(f"\nConversion Summary:")
    print(f"Successful conversions: {successful_conversions}")
    print(f"Failed conversions: {failed_conversions}")
    print(f"Total files processed: {len(input_files)}")

input_dir = "../files/augmented_data"  # Your augmented files directory
output_dir = "files/augmented_data"  # Where to save simplified files

# Convert all files
batch_convert_files(input_dir, output_dir)

def verify_conversion(original_file, simplified_file):
    """
    Verify that the conversion maintained data integrity.
    
    Args:
        original_file (str): Path to original full format file
        simplified_file (str): Path to converted simple format file
    """
    try:
        # Read original file
        with open(original_file, 'r') as f:
            orig_lines = f.readlines()[1:]  # Skip header
        
        # Read simplified file
        with open(simplified_file, 'r') as f:
            simp_lines = f.readlines()
        
        if len(orig_lines) != len(simp_lines):
            print(f"Warning: Line count mismatch. Original: {len(orig_lines)}, Simplified: {len(simp_lines)}")
        
        # Check some random lines
        num_lines = min(len(orig_lines), len(simp_lines))
        check_indices = np.random.choice(num_lines, min(5, num_lines), replace=False)
        
        for idx in check_indices:
            orig_fields = orig_lines[idx].strip().split()
            simp_fields = simp_lines[idx].strip().split()
            
            # Compare values
            orig_date = orig_fields[1]
            orig_east = float(orig_fields[8])
            orig_north = float(orig_fields[10])
            orig_up = float(orig_fields[12])
            
            simp_date = simp_fields[0]
            simp_east = float(simp_fields[1])
            simp_north = float(simp_fields[2])
            simp_up = float(simp_fields[3])
            
            print(f"\nChecking line {idx+1}:")
            print(f"Original: {orig_date} {orig_east:.6f} {orig_north:.6f} {orig_up:.6f}")
            print(f"Simplified: {simp_date} {simp_east:.6f} {simp_north:.6f} {simp_up:.6f}")
            
    except Exception as e:
        print(f"Error during verification: {str(e)}")

Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out of range
Error processing line: 
Error details: list index out o

# NRMSE

In [27]:
from glob import glob

def read_tenv3_file(file_path):
    df = pd.read_csv(file_path, sep='\s+', header=None, 
                    names=['YYMMMDD', '__east(m)', '_north(m)', '____up(m)'])
    
    return df[['__east(m)', '_north(m)', '____up(m)']]

def calculate_nrmse(original, predicted):
    """Calculate NRMSE using the SVC approach"""
    if original.shape != predicted.shape:
        raise ValueError("The shapes of the original and predicted datasets must match.")
    mse = np.mean((original - predicted) ** 2)
    rmse = np.sqrt(mse)
    nrmse = rmse / (np.max(original) - np.min(original))
    return nrmse

def get_matching_augmented_files(original_file, augmented_folder):
    """Find matching augmented files for an original GPS file"""
    base_name = os.path.basename(original_file)
    base_name_without_ext = os.path.splitext(base_name)[0]
    pattern = os.path.join(augmented_folder, f"synthetic_{base_name_without_ext}*.tenv3")
    matching_files = glob(pattern)
    
    def sort_key(filename):
        match = re.search(r'\((\d+)\)', filename)
        return int(match.group(1)) if match else -1
    
    return sorted(matching_files, key=sort_key)

def process_gps_files(original_folder, augmented_folder, input_filenames):
    """Process GPS files and calculate NRMSE metrics"""
    nrmse_results = {}
    
    input_filenames_set = {os.path.splitext(os.path.basename(filename))[0] 
                          for filename in input_filenames}
    
    for original_file in glob(os.path.join(original_folder, "*.tenv3")):
        base_name = os.path.splitext(os.path.basename(original_file))[0]
        
        if base_name not in input_filenames_set:
            continue
        
        original_data = read_tenv3_file(original_file)
        matching_augmented_files = get_matching_augmented_files(original_file, augmented_folder)
        
        file_nrmse = []  # Store NRMSE values for each augmented file
        for augmented_file in matching_augmented_files:
            augmented_data = read_tenv3_file(augmented_file)
            
            # Ensure both datasets have the same length
            min_length = min(len(original_data), len(augmented_data))
            original_array = original_data.iloc[:min_length].values
            augmented_array = augmented_data.iloc[:min_length].values

            # print(f"og array: {original_array}")
            # print(f"aug array: {augmented_array}")
            
            try:
                nrmse = calculate_nrmse(original_array, augmented_array)
                file_nrmse.append(nrmse)
            except Exception as e:
                print(f"Error calculating NRMSE for {augmented_file}: {str(e)}")
                continue
        
        if file_nrmse:  # Only store results if we have valid NRMSE values
            nrmse_results[os.path.basename(original_file)] = file_nrmse
    
    return nrmse_results

def save_results_to_log(results, output_path):
    with open(output_path, 'w') as log_file:
        for original_file, nrmse_values in results.items():
            avg_nrmse = None
            if len(nrmse_values) > 1:
                avg_nrmse = np.mean(nrmse_values)

            nrmse_values_str = ", ".join([f"{nrmse:.4f}" for nrmse in nrmse_values])
            log_line = f"{original_file}: NRMSE = {nrmse_values_str}"
            if avg_nrmse is not None:
                log_line += f", Avg NRMSE: {avg_nrmse:.4f}"

            log_file.write(log_line + '\n')
            print(log_line)

# Main execution
original_folder = "imputed"
augmented_folder = "files/augmented_data"
output_log_file = "nrmse_results_log.txt"

# Process files and save results
results = process_gps_files(original_folder, augmented_folder, input_filenames)
save_results_to_log(results, output_log_file)

all_nrmse_values = [nrmse for nrmse_list in results.values() for nrmse in nrmse_list]
overall_avg_nrmse = np.mean(all_nrmse_values) if all_nrmse_values else None
overall_std_nrmse = np.std(all_nrmse_values) if all_nrmse_values else None

# Print and save the overall average NRMSE and standard deviation
with open(output_log_file, 'a') as log_file:
    if overall_avg_nrmse is not None and overall_std_nrmse is not None:
        log_line = f"\nOverall Average NRMSE: {overall_avg_nrmse:.4f}, Standard Deviation: {overall_std_nrmse:.4f}"
    else:
        log_line = "No NRMSE values calculated."

    log_file.write(log_line + '\n')
    print(log_line)

<>:4: SyntaxWarning: invalid escape sequence '\s'
<>:4: SyntaxWarning: invalid escape sequence '\s'
C:\Users\Grimes\AppData\Local\Temp\ipykernel_1520\3095704035.py:4: SyntaxWarning: invalid escape sequence '\s'
  df = pd.read_csv(file_path, sep='\s+', header=None,


BLAS.tenv3: NRMSE = 0.0121
DGJG.tenv3: NRMSE = 0.0054
DKSG.tenv3: NRMSE = 0.0357
HJOR.tenv3: NRMSE = 0.0043
HMBG.tenv3: NRMSE = 0.0028
HRDG.tenv3: NRMSE = 0.0046
JGBL.tenv3: NRMSE = 0.0046
JWLF.tenv3: NRMSE = 0.0120
KMJP.tenv3: NRMSE = 0.0088
KMOR.tenv3: NRMSE = 0.0027
KUAQ.tenv3: NRMSE = 0.0119
KULL.tenv3: NRMSE = 0.0182
LBIB.tenv3: NRMSE = 0.0093
LEFN.tenv3: NRMSE = 0.0051
MARG.tenv3: NRMSE = 0.0047
MSVG.tenv3: NRMSE = 0.0066
NRSK.tenv3: NRMSE = 0.0073
QAAR.tenv3: NRMSE = 0.0174
UTMG.tenv3: NRMSE = 0.0541
YMER.tenv3: NRMSE = 0.0018

Overall Average NRMSE: 0.0115, Standard Deviation: 0.0124


# Post Hoc Discriminative Score

In [31]:
import os
from glob import glob
import numpy as np
import logging
from sklearn.metrics import accuracy_score
from sklearn.model_selection import KFold
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense

# Configure logging
log_filename = "posthoc_discriminative_score.txt"
logging.basicConfig(
    level=logging.INFO,
    format="%(message)s",
    handlers=[
        logging.FileHandler(log_filename, mode="w", encoding="utf-8"),
        logging.StreamHandler()
    ]
)

def process_files(original_folder, augmented_folder, input_filenames):
    all_real_data = []
    all_synthetic_data = []
    input_filenames_set = {os.path.splitext(os.path.basename(filename))[0] for filename in input_filenames}
    
    for original_file in glob(os.path.join(original_folder, "*.tenv3")):
        base_name = os.path.splitext(os.path.basename(original_file))[0]
        
        if base_name not in input_filenames_set:
            continue
        
        original_data = read_tenv3_file(original_file)
        all_real_data.append(original_data.values)
        
        matching_augmented_files = get_matching_augmented_files(original_file, augmented_folder)
        
        for augmented_file in matching_augmented_files:
            augmented_data = read_tenv3_file(augmented_file)
            all_synthetic_data.append(augmented_data.values)
    
    return np.concatenate(all_real_data), np.concatenate(all_synthetic_data)

def create_lstm_classifier(input_shape):
    model = Sequential([
        LSTM(64, input_shape=input_shape, return_sequences=True),
        LSTM(32),
        Dense(1, activation='sigmoid')
    ])
    model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
    return model

def prepare_data_for_lstm(real_data, synthetic_data):
    n_features = min(real_data.shape[1], synthetic_data.shape[1])
    real_data_trimmed = real_data[:, :n_features]
    synthetic_data_trimmed = synthetic_data[:, :n_features]
    
    X = np.vstack((real_data_trimmed, synthetic_data_trimmed))
    y = np.concatenate((np.ones(len(real_data)), np.zeros(len(synthetic_data))))
    return X, y

def post_hoc_discriminative_score(real_data, synthetic_data, n_splits=10):
    X, y = prepare_data_for_lstm(real_data, synthetic_data)
    kf = KFold(n_splits=n_splits, shuffle=True, random_state=42)
    accuracies = []
    
    for fold, (train_index, test_index) in enumerate(kf.split(X), start=1):
        logging.info(f"\nFold {fold}/{n_splits}:")
        
        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = y[train_index], y[test_index]
        
        X_train = X_train.reshape((X_train.shape[0], 1, X_train.shape[1]))
        X_test = X_test.reshape((X_test.shape[0], 1, X_test.shape[1]))
        
        model = create_lstm_classifier((1, X_train.shape[2]))
        
        # Train model and log epoch progress
        history = model.fit(X_train, y_train, epochs=5, batch_size=512, verbose=0)
        for epoch, metrics in enumerate(history.history["accuracy"], start=1):
            logging.info(f"  Epoch {epoch}: Accuracy = {metrics:.4f}")
        
        y_pred = (model.predict(X_test) > 0.5).astype(int)
        accuracy = accuracy_score(y_test, y_pred)
        accuracies.append(accuracy)
    
    mean_accuracy = np.mean(accuracies)
    std_accuracy = np.std(accuracies)
    logging.info(f"\nMean accuracy: {mean_accuracy:.4f}, Standard Deviation: {std_accuracy:.4f}")
    return mean_accuracy, std_accuracy

# Specify your folders
original_folder = "imputed"
augmented_folder = "files/augmented_data" #Directory ng augmented data


# Process files
real_data, synthetic_data = process_files(original_folder, augmented_folder, input_filenames)

# Compute post-hoc discriminative score
mean_accuracy, std_accuracy = post_hoc_discriminative_score(real_data, synthetic_data)


Fold 1/10:
c:\Users\Grimes\OneDrive\Desktop\tryyy\.venv\Lib\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
  Epoch 1: Accuracy = 0.5168
  Epoch 2: Accuracy = 0.5174
  Epoch 3: Accuracy = 0.5172
  Epoch 4: Accuracy = 0.5175
  Epoch 5: Accuracy = 0.5175


716/716 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step



Fold 2/10:
c:\Users\Grimes\OneDrive\Desktop\tryyy\.venv\Lib\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
  Epoch 1: Accuracy = 0.5175
  Epoch 2: Accuracy = 0.5176
  Epoch 3: Accuracy = 0.5176
  Epoch 4: Accuracy = 0.5176
  Epoch 5: Accuracy = 0.5177


716/716 ━━━━━━━━━━━━━━━━━━━━ 2s 2ms/step



Fold 3/10:
c:\Users\Grimes\OneDrive\Desktop\tryyy\.venv\Lib\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
  Epoch 1: Accuracy = 0.5171
  Epoch 2: Accuracy = 0.5171
  Epoch 3: Accuracy = 0.5170
  Epoch 4: Accuracy = 0.5171
  Epoch 5: Accuracy = 0.5176


...


Fold 9/10:
c:\Users\Grimes\OneDrive\Desktop\tryyy\.venv\Lib\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
  Epoch 1: Accuracy = 0.5165
  Epoch 2: Accuracy = 0.5164
  Epoch 3: Accuracy = 0.5167
  Epoch 4: Accuracy = 0.5166
  Epoch 5: Accuracy = 0.5166


716/716 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step



Fold 10/10:
c:\Users\Grimes\OneDrive\Desktop\tryyy\.venv\Lib\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
  Epoch 1: Accuracy = 0.5169
  Epoch 2: Accuracy = 0.5168
  Epoch 3: Accuracy = 0.5170
  Epoch 4: Accuracy = 0.5169
  Epoch 5: Accuracy = 0.5170


716/716 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step



Mean accuracy: 0.5171, Standard Deviation: 0.0026


# Post Hoc Predictive Score

In [34]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from xgboost import XGBRegressor
from glob import glob
import os
import time

def write_to_log(message):
    """Write a message to the log file."""
    log_file = "posthoc_predictive_score.txt"
    with open(log_file, "a") as f:
        f.write(message + "\n")

def read_svc_file(file_path):
    """Read an SVC file and return its contents as a DataFrame."""
    try:
        df = pd.read_csv(file_path, sep=' ', header=None)
        if df.empty:
            return None
        df = df.iloc[:, 1:]
        return df
    except Exception as e:
        return None

def get_matching_augmented_file(original_file, augmented_folder):
    """Get matching augmented file for a given original file."""
    base_name = os.path.splitext(os.path.basename(original_file))[0]
    augmented_file = os.path.join(augmented_folder, f"synthetic_{base_name}.tenv3")
    return augmented_file if os.path.exists(augmented_file) else None

def process_files(original_folder, augmented_folder):
    """Process original and augmented files and prepare them for analysis."""
    paired_data = []
    for original_file in glob(os.path.join(original_folder, "*.tenv3")):
        augmented_file = get_matching_augmented_file(original_file, augmented_folder)
        if augmented_file is None:
            continue
            
        original_data = read_svc_file(original_file)
        augmented_data = read_svc_file(augmented_file)
        
        if (original_data is not None and augmented_data is not None and 
            original_data.shape[1] == augmented_data.shape[1]):
            paired_data.append((original_file, augmented_file))

    if not paired_data:
        raise ValueError("No valid data pairs found for processing")
    return paired_data

def prepare_sequences(data, time_steps=4):
    """Prepare sequences for prediction, using all but last timestep as input."""
    X, y = [], []
    for i in range(len(data) - time_steps):
        X.append(data[i:i + time_steps - 1].flatten())
        y.append(data[i + time_steps - 1])
    return np.array(X), np.array(y)

def evaluate_synthetic_data(original_file, synthetic_file):
    """Evaluate a single synthetic dataset against its original counterpart."""
    original_df = read_svc_file(original_file)
    synthetic_df = read_svc_file(synthetic_file)

    if original_df is None or synthetic_df is None:
        return None

    integer_columns = [0, 1, 4, 5]
    scaler = MinMaxScaler()
    original_scaled = scaler.fit_transform(original_df)
    synthetic_scaled = scaler.transform(synthetic_df)

    start_time = time.time()
    X_train, y_train = prepare_sequences(synthetic_scaled)
    X_test, y_test = prepare_sequences(original_scaled)

    if len(X_train) == 0 or len(X_test) == 0:
        return None

    mapes_per_dim = []
    for dim in range(y_train.shape[1]):
        model = XGBRegressor(
            n_estimators=100,
            learning_rate=0.1,
            max_depth=6,
            random_state=42
        )

        model.fit(X_train, y_train[:, dim], verbose=False)
        y_pred = model.predict(X_test)

        y_true_original = original_df.iloc[len(original_df)-len(y_test):, dim].values

        temp_data = np.zeros((len(y_pred), original_df.shape[1]))
        temp_data[:, dim] = y_pred
        y_pred_original = scaler.inverse_transform(temp_data)[:, dim]

        if dim in integer_columns:
            y_pred_original = np.round(y_pred_original)

        if dim == 3:
            y_pred_original = np.round(y_pred_original)

        y_pred_original = np.round(y_pred_original).astype(int)
        y_true_original = np.round(y_true_original).astype(int)

        errors = []
        for true, pred in zip(y_true_original, y_pred_original):
            if true == 0:
                errors.append(100 if pred != 0 else 0)
            else:
                errors.append(min(abs((true - pred) / true) * 100, 100))

        mapes_per_dim.append(np.mean(errors))

    elapsed_time = time.time() - start_time
    return np.mean(mapes_per_dim), elapsed_time

def post_hoc_predictive_score(original_folder, augmented_folder):
    """Calculate post-hoc predictive score for all pairs of original and synthetic data."""
    try:
        paired_files = process_files(original_folder, augmented_folder)
        all_results = []
        
        for original_file, synthetic_file in paired_files:
            result = evaluate_synthetic_data(original_file, synthetic_file)
            if result is not None:
                mape, elapsed_time = result
                file_name = os.path.basename(original_file)
                log_message = (f"Processing: {file_name} Completed in {elapsed_time:.1f}s "
                               f"(MAPE: {mape:.2f}%)")
                print(log_message)
                write_to_log(log_message)
                all_results.append(mape)
        
        if not all_results:
            raise ValueError("No valid results calculated")
        
        summary_message = (f"----------------------------------------\n"
                           f"Overall Results:\n"
                           f"Average MAPE: {np.mean(all_results):.2f}%, "
                           f"Standard Deviation: {np.std(all_results):.2f}%")
        print(summary_message)
        write_to_log(summary_message)
        
        return np.mean(all_results), np.std(all_results)
        
    except Exception as e:
        error_message = f"Error: {str(e)}"
        print(error_message)
        write_to_log(error_message)
        return None, None

def main():
    try:
        original_folder = "imputed"
        augmented_folder = "files/augmented_data" #Directory ng augmented data
        post_hoc_predictive_score(original_folder, augmented_folder) 
            
    except Exception as e:
        error_message = f"Error: {str(e)}"
        print(error_message)
        write_to_log(error_message)

if __name__ == "__main__":
    main()

Processing: BLAS.tenv3 Completed in 1.2s (MAPE: 0.73%)
Processing: DGJG.tenv3 Completed in 0.8s (MAPE: 0.00%)
Processing: DKSG.tenv3 Completed in 0.6s (MAPE: 0.18%)
Processing: HJOR.tenv3 Completed in 0.6s (MAPE: 0.92%)
Processing: HMBG.tenv3 Completed in 0.6s (MAPE: 0.49%)
Processing: HRDG.tenv3 Completed in 0.5s (MAPE: 0.00%)
Processing: JGBL.tenv3 Completed in 0.5s (MAPE: 0.00%)
Processing: JWLF.tenv3 Completed in 0.5s (MAPE: 0.00%)
Processing: KMJP.tenv3 Completed in 0.5s (MAPE: 0.00%)
Processing: KMOR.tenv3 Completed in 0.8s (MAPE: 0.21%)
Processing: KUAQ.tenv3 Completed in 0.9s (MAPE: 0.14%)
Processing: KULL.tenv3 Completed in 0.8s (MAPE: 0.38%)
Processing: LBIB.tenv3 Completed in 1.5s (MAPE: 5.09%)
Processing: LEFN.tenv3 Completed in 1.2s (MAPE: 0.00%)
Processing: MARG.tenv3 Completed in 1.8s (MAPE: 0.00%)
Processing: MSVG.tenv3 Completed in 1.5s (MAPE: 0.00%)
Processing: NRSK.tenv3 Completed in 1.1s (MAPE: 0.00%)
Processing: QAAR.tenv3 Completed in 0.6s (MAPE: 0.00%)
Processing